In [46]:
from datetime import date, datetime, timedelta, time
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

In [47]:
path = "data/yellow_tripdata_2019-06.csv"
df = pd.read_csv(path, parse_dates=["tpep_pickup_datetime", "tpep_dropoff_datetime"], low_memory=False)

In [48]:
zones = pd.read_csv('taxiZoneLookup.csv')#, index_col="LocationID")

In [49]:
df = df[["tpep_pickup_datetime", "tpep_dropoff_datetime", "PULocationID", "DOLocationID", 
         "trip_distance", "passenger_count"]]

In [50]:
df.rename(columns={"PULocationID": "LocationID"}, inplace=True)
df = pd.merge(df, zones[["LocationID", "Borough"]], on="LocationID", how="left")
df = pd.merge(df, zones[["LocationID", "Zone"]], on="LocationID", how="left")
df.rename(columns={"LocationID": "PULocationID", "Borough": "PUBorough", "Zone": "PUZone"}, inplace=True)

In [51]:
df.rename(columns={"DOLocationID": "LocationID"}, inplace=True)
df = pd.merge(df, zones[["LocationID", "Borough"]], on="LocationID", how="left")
df = pd.merge(df, zones[["LocationID", "Zone"]], on="LocationID", how="left")
df.rename(columns={"LocationID": "DOLocationID", "Borough": "DOBorough", "Zone": "DOZone"}, inplace=True)

In [52]:
df = df[df.PUBorough=="Manhattan"]

In [53]:
df

tpep_pickup_datetime tpep_dropoff_datetime  PULocationID  \
1        2019-06-01 00:06:31   2019-06-01 00:06:52           262   
2        2019-06-01 00:17:05   2019-06-01 00:36:38            74   
4        2019-06-01 00:03:25   2019-06-01 00:15:42           113   
5        2019-06-01 00:28:31   2019-06-01 00:39:23            79   
6        2019-06-01 00:46:46   2019-06-01 00:50:55           211   
...                      ...                   ...           ...   
6941019  2019-06-30 23:23:03   2019-06-30 23:39:48            68   
6941020  2019-06-30 23:50:22   2019-06-30 23:57:01           246   
6941021  2019-06-30 23:58:32   2019-07-01 00:00:42            90   
6941022  2019-06-30 23:23:10   2019-06-30 23:30:45           140   
6941023  2019-06-30 23:39:13   2019-06-30 23:44:56           142   

         DOLocationID  trip_distance  passenger_count  PUBorough  \
1                 263           0.00                1  Manhattan   
2                   7           4.40                1  Manhattan   
4                 148           1.70                1  Manhattan   
5                 125           1.60                2  Manhattan   
6                 148           0.60                4  Manhattan   
...               ...            ...              ...        ...   
6941019           158           0.90                1  Manhattan   
6941020            90           0.50                1  Manhattan   
6941021           186           0.20                1  Manhattan   
6941022           163           1.38                1  Manhattan   
6941023           151           1.77                2  Manhattan   

                            PUZone  DOBorough                         DOZone  
1                   Yorkville East  Manhattan                 Yorkville West  
2                East Harlem North     Queens                        Astoria  
4          Greenwich Village North  Manhattan                Lower East Side  
5                     East Village  Manhattan                      Hudson Sq  
6                             SoHo  Manhattan                Lower East Side  
...                            ...        ...                            ...  
6941019               East Chelsea  Manhattan  Meatpacking/West Village West  
6941020  West Chelsea/Hudson Yards  Manhattan                       Flatiron  
6941021                   Flatiron  Manhattan   Penn Station/Madison Sq West  
6941022            Lenox Hill East  Manhattan                  Midtown North  
6941023        Lincoln Square East  Manhattan               Manhattan Valley  

[6267971 rows x 10 columns]

In [54]:
#df.loc[df.PUZone=="JFK Airport", "PUBorough"] = "JFK"
#df.loc[df.PUZone=="LaGuardia Airport", "PUBorough"] = "LaGuardia"

In [55]:
#df.loc[df.DOZone=="JFK Airport", "DOBorough"] = "JFK"
#df.loc[df.DOZone=="LaGuardia Airport", "DOBorough"] = "LaGuardia"

In [56]:
df["tpep_pickup_datetime"] = df["tpep_pickup_datetime"].apply(lambda x: x - timedelta(minutes=x.minute % 60, seconds=x.second))

In [57]:
#df = df[["tpep_pickup_datetime", "PUBorough", "DOBorough"]]

In [58]:
#df = df[(df.PUBorough!="Unknown") & (df.DOBorough!="Unknown")]

In [59]:
#df = df[]

In [60]:
#df["from_to"] = df.PUBorough + "-" + df.DOBorough

In [61]:
#df = df[["tpep_pickup_datetime", "from_to"]]

In [62]:
#df = pd.concat([df.tpep_pickup_datetime, pd.get_dummies(df.from_to)], axis=1)

In [63]:
def fullRun(years, df):
    check = 1
    for year in years:
        #print(year)
        for month in range(6,7):
            date_str = str(year)+"-"+str(month)
            #print(date_str)
            """
            path = "data/yellow_tripdata_{}-{}{}".format(year, f"{month:02d}", ".csv")
            
            df = pd.read_csv(path, 
                             parse_dates=["tpep_pickup_datetime", "tpep_dropoff_datetime"], 
                             #index_col=["tpep_pickup_datetime"], 
                             #low_memory=False
                            )
            """            
            start = datetime(year,month,1)
            if month != 12:
                end = datetime(year,month+1,1)
            else:
                end = datetime(year+1,1,1)
            
            df = df[(df.tpep_pickup_datetime>=start) & (df.tpep_pickup_datetime<end)]

            df = df[["tpep_pickup_datetime",
                     "tpep_dropoff_datetime",
                     "trip_distance", 
                     "passenger_count",
                     "PUZone"]
                   ]
            
            df = df[df.trip_distance < 100]
            df = df[df.passenger_count != 0]
            
            df["trip_duration"] = df["tpep_dropoff_datetime"] - df["tpep_pickup_datetime"]
            df = df[(df.trip_duration > timedelta(minutes=1)) & (df.trip_duration < timedelta(hours=3))]
            
            df = df[["tpep_pickup_datetime", "PUZone"]]
            
            df["year"] = df["tpep_pickup_datetime"].apply(lambda x: x.year)
            df["month"] = df["tpep_pickup_datetime"].apply(lambda x: x.month)
            df["day"] = df["tpep_pickup_datetime"].apply(lambda x: x.day)
            df["hour"] = df["tpep_pickup_datetime"].apply(lambda x: x.hour)
            df["wday"] = df["tpep_pickup_datetime"].apply(lambda x: x.weekday())
            
            df = df.drop("tpep_pickup_datetime", axis=1)
            df["rides"] = 0
            
            df = df.groupby(["PUZone", "year", "month", "day", "hour", "wday"]).agg("count")
            df.reset_index(inplace=True)  
            
            if check == 0:
                final = pd.concat([final, df], sort=False)
            else:
                final = df
                check = 0
            print(str(year) + "-" + str(month) + " done!")
                
    return final

In [64]:
df = fullRun([2019], df)

2019-6 done!


In [65]:
df

PUZone  year  month  day  hour  wday  rides
0       Alphabet City  2019      6    1     0     5     69
1       Alphabet City  2019      6    1     1     5     71
2       Alphabet City  2019      6    1     2     5     56
3       Alphabet City  2019      6    1     3     5     34
4       Alphabet City  2019      6    1     4     5     22
...               ...   ...    ...  ...   ...   ...    ...
43986  Yorkville West  2019      6   30    19     6    167
43987  Yorkville West  2019      6   30    20     6    129
43988  Yorkville West  2019      6   30    21     6    148
43989  Yorkville West  2019      6   30    22     6    120
43990  Yorkville West  2019      6   30    23     6     84

[43991 rows x 7 columns]

In [66]:
df['dt'] = df[['year', 'month', 'day', 'hour']].apply(lambda s : datetime(*s),axis = 1)

In [67]:
df = df[["PUZone", "dt", "rides"]]

In [68]:
df["dt"] = df["dt"].apply(lambda x: x.strftime("%m/%d/%Y, %H:%M:%S"))

<ipython-input-68-db41b6b1bd30>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["dt"] = df["dt"].apply(lambda x: x.strftime("%m/%d/%Y, %H:%M:%S"))


In [69]:
df["dt"] = df["dt"].apply(lambda x: pd.to_datetime(x))
df[df.dt < datetime(2019,6,6)]
df["dt"] = df["dt"].apply(lambda x: x.strftime("%m/%d/%Y, %H:%M:%S"))

<ipython-input-69-7533e6092bac>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["dt"] = df["dt"].apply(lambda x: pd.to_datetime(x))
<ipython-input-69-7533e6092bac>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["dt"] = df["dt"].apply(lambda x: x.strftime("%m/%d/%Y, %H:%M:%S"))


In [ ]:
import plotly.express as px
from vega_datasets import data
#df = data.disasters()
#df = df[df.Year > 1990]
fig = px.bar(df,
             y="PUZone",
             x="rides",
             animation_frame="dt",
             orientation='h',
             range_x=[0, df.rides.max()],
             color="PUZone")
# improve aesthetics (size, grids etc.)
fig.update_layout(width=800,
                  height=1600,
                  xaxis_showgrid=False,
                  yaxis_showgrid=False,
                  paper_bgcolor='rgba(0,0,0,0)',
                  plot_bgcolor='rgba(0,0,0,0)',
                  title_text='NYC Taxi Ride Pickup Distribution',
                  showlegend=False)
fig.update_xaxes(title_text='Number of Rides')
fig.update_yaxes(title_text='')
fig.write_html("pu_distr.html")
fig.show()

In [ ]:
df

In [70]:
df = df.loc[~df['PUZone'].isin(["Bronx", "EWR", "Staten Island"])]

In [71]:
df

PUZone                    dt  rides
0       Alphabet City  06/01/2019, 00:00:00     69
1       Alphabet City  06/01/2019, 01:00:00     71
2       Alphabet City  06/01/2019, 02:00:00     56
3       Alphabet City  06/01/2019, 03:00:00     34
4       Alphabet City  06/01/2019, 04:00:00     22
...               ...                   ...    ...
43986  Yorkville West  06/30/2019, 19:00:00    167
43987  Yorkville West  06/30/2019, 20:00:00    129
43988  Yorkville West  06/30/2019, 21:00:00    148
43989  Yorkville West  06/30/2019, 22:00:00    120
43990  Yorkville West  06/30/2019, 23:00:00     84

[43991 rows x 3 columns]

In [72]:
df["dt"] = df["dt"].apply(lambda x: pd.to_datetime(x))

In [28]:
df["time"] = df["dt"].apply(lambda x: time(x.hour))

<ipython-input-28-d1666a6979b2>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["time"] = df["dt"].apply(lambda x: time(x.hour))


In [36]:
df["dt"] = df["dt"].apply(lambda x: x.date())

<ipython-input-36-d463bd092616>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["dt"] = df["dt"].apply(lambda x: x.date())


In [43]:
df1 = df[df.dt==date(2019,6,1) & (df["time"]==time(18,0))]

TypeError: Cannot perform 'rand_' with a dtyped [bool] array and scalar of type [bool]

In [76]:
df1 = df[df.dt==datetime(2019,6,1,18,0)]

In [77]:
df1

PUZone                  dt  rides
18                 Alphabet City 2019-06-01 18:00:00     28
725                 Battery Park 2019-06-01 18:00:00     29
1273           Battery Park City 2019-06-01 18:00:00    157
1989                Bloomingdale 2019-06-01 18:00:00     71
2708              Central Harlem 2019-06-01 18:00:00     59
...                          ...                 ...    ...
40414  West Chelsea/Hudson Yards 2019-06-01 18:00:00    329
41134               West Village 2019-06-01 18:00:00    283
41854         World Trade Center 2019-06-01 18:00:00    120
42573             Yorkville East 2019-06-01 18:00:00    162
43289             Yorkville West 2019-06-01 18:00:00    312

[63 rows x 3 columns]

In [79]:
path = "data/yellow_tripdata_2019-06.csv"
df2 = pd.read_csv(path, parse_dates=["tpep_pickup_datetime", "tpep_dropoff_datetime"], low_memory=False)

In [81]:
df2.rename(columns={"PULocationID": "LocationID"}, inplace=True)
df2 = pd.merge(df2, zones[["LocationID", "Borough"]], on="LocationID", how="left")
df2 = pd.merge(df2, zones[["LocationID", "Zone"]], on="LocationID", how="left")
df2.rename(columns={"LocationID": "PULocationID", "Borough": "PUBorough", "Zone": "PUZone"}, inplace=True)

In [84]:
df2 = df2[["tpep_pickup_datetime", "PUZone"]]

In [86]:
df2["tpep_pickup_datetime"] = df2["tpep_pickup_datetime"].apply(lambda x: x - timedelta(minutes=x.minute % 60, seconds=x.second))

<ipython-input-86-3c309f16e736>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [89]:
df3 = df2[df2.tpep_pickup_datetime==datetime(2019,6,1,18,0)]

In [91]:
df3["time"] = df3["tpep_pickup_datetime"].apply(lambda x: x.time())

<ipython-input-91-1659c78ca9e7>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [94]:
df2["time"] = df2["tpep_pickup_datetime"].apply(lambda x: x.time())
df2["date"] = df2["tpep_pickup_datetime"].apply(lambda x: x.date())

<ipython-input-94-c9f2bfce1622>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-94-c9f2bfce1622>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [99]:
df4 = df2[df2.date==date(2019,6,1)]

In [100]:
df4

tpep_pickup_datetime                          PUZone      time  \
0       2019-06-01 00:00:00  Long Island City/Hunters Point  00:00:00   
1       2019-06-01 00:00:00                  Yorkville East  00:00:00   
2       2019-06-01 00:00:00               East Harlem North  00:00:00   
3       2019-06-01 00:00:00  Long Island City/Hunters Point  00:00:00   
4       2019-06-01 00:00:00         Greenwich Village North  00:00:00   
...                     ...                             ...       ...   
445911  2019-06-01 12:00:00           Upper West Side North  12:00:00   
445912  2019-06-01 12:00:00                    East Chelsea  12:00:00   
445913  2019-06-01 12:00:00                   Midtown North  12:00:00   
445914  2019-06-01 12:00:00                  Midtown Center  12:00:00   
452996  2019-06-01 13:00:00       West Chelsea/Hudson Yards  13:00:00   

              date  
0       2019-06-01  
1       2019-06-01  
2       2019-06-01  
3       2019-06-01  
4       2019-06-01  
...            ...  
445911  2019-06-01  
445912  2019-06-01  
445913  2019-06-01  
445914  2019-06-01  
452996  2019-06-01  

[244836 rows x 4 columns]

In [169]:
'''
import plotly.express as px

fig = px.bar(df,
             y="PUZone",
             x="rides",
             animation_frame="dt",
             orientation='h',
             range_x=[0, df.rides.max()],
             color="PUZone")
'''





import plotly.express as px

fig = px.density_heatmap(df11,
                         x="time",
                         y="PUZone",
                         z="rides",
                         histfunc="avg",
                         animation_frame="date"
                        )

fig.update_layout(width=700,
                  height=600,
                  xaxis_showgrid=False,
                  yaxis_showgrid=False,
                  paper_bgcolor='rgba(0,0,0,0)',
                  plot_bgcolor='rgba(0,0,0,0)',
                  title_text='NYC Taxi Ride Pickup Distribution',
                  showlegend=False)
fig.update_xaxes(title_text='')
fig.update_yaxes(title_text='', showticklabels=False)

fig.write_html("pu_distr1.html")
fig.show()

In [154]:
df11[df11.date==date(2019,6,7)]

Empty DataFrame
Columns: [PUZone, rides, time, date]
Index: []

In [105]:
df["time"] = df["dt"].apply(lambda x: x.time())
df["date"] = df["dt"].apply(lambda x: x.date())

In [108]:
df5 = df[df.date==date(2019,6,1)]

In [111]:
df5.PUZone.nunique()

66

In [140]:
df11 = df.drop("dt", axis=1)

In [136]:
df11.date[0]

datetime.date(2019, 6, 1)

In [141]:
df11["date"] = df11["date"].apply(lambda x: x.strftime("%m/%d/%Y"))

In [150]:
df11["time"] = df11["time"].apply(lambda x: x.strftime("%H:%M"))

In [157]:
df11

PUZone  rides   time        date
0       Alphabet City     69  00:00  06/01/2019
1       Alphabet City     71  01:00  06/01/2019
2       Alphabet City     56  02:00  06/01/2019
3       Alphabet City     34  03:00  06/01/2019
4       Alphabet City     22  04:00  06/01/2019
...               ...    ...    ...         ...
43986  Yorkville West    167  19:00  06/30/2019
43987  Yorkville West    129  20:00  06/30/2019
43988  Yorkville West    148  21:00  06/30/2019
43989  Yorkville West    120  22:00  06/30/2019
43990  Yorkville West     84  23:00  06/30/2019

[43991 rows x 4 columns]

In [164]:
df[df.date==date(2019,6,7)]

PUZone                  dt  rides      time        date
144     Alphabet City 2019-06-07 00:00:00     28  00:00:00  2019-06-07
145     Alphabet City 2019-06-07 01:00:00     14  01:00:00  2019-06-07
146     Alphabet City 2019-06-07 02:00:00     11  02:00:00  2019-06-07
147     Alphabet City 2019-06-07 03:00:00      3  03:00:00  2019-06-07
148     Alphabet City 2019-06-07 04:00:00      2  04:00:00  2019-06-07
...               ...                 ...    ...       ...         ...
43434  Yorkville West 2019-06-07 19:00:00    272  19:00:00  2019-06-07
43435  Yorkville West 2019-06-07 20:00:00    217  20:00:00  2019-06-07
43436  Yorkville West 2019-06-07 21:00:00    227  21:00:00  2019-06-07
43437  Yorkville West 2019-06-07 22:00:00    206  22:00:00  2019-06-07
43438  Yorkville West 2019-06-07 23:00:00    177  23:00:00  2019-06-07

[1466 rows x 5 columns]